In [2]:
import vectorbtpro as vbt
from numba import njit

/Users/ericervin/opt/anaconda3/envs/datascience/lib/python3.10/site-packages/numba/core/decorators.py:262: NumbaDeprecationWarning: numba.generated_jit is deprecated. Please see the documentation at: https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-generated-jit for more information and advice on a suitable replacement.
  warnings.warn(msg, NumbaDeprecationWarning)


In [3]:
# From documentation. this clarifies quite a bit
# Enter randomly, exit randomly but only if in profit
@njit
def signal_func_nb(c, entries, exits):
    is_entry = vbt.pf_nb.select_nb(c, entries)
    is_exit = vbt.pf_nb.select_nb(c, exits)
    if is_entry:
        return True, False, False, False
    if is_exit:
        pos_info = c.last_pos_info[c.col]
        if pos_info["status"] == vbt.pf_enums.TradeStatus.Open:
            if pos_info["pnl"] >= 0:
                return False, True, False, False
    return False, False, False, False

data = vbt.YFData.fetch("BTC-USD")
entries, exits = data.run("RANDNX", n=10, unpack=True)
pf = vbt.Portfolio.from_signals(
    data,
    signal_func_nb=signal_func_nb,
    signal_args=(vbt.Rep("entries"), vbt.Rep("exits")),
    broadcast_named_args=dict(entries=entries, exits=exits),
    jitted=False  
)
pf.trades.records_readable[["Entry Index", "Exit Index", "PnL"]]

Entry Index                Exit Index           PnL
0 2015-02-19 00:00:00+00:00 2018-01-27 00:00:00+00:00   4661.343902
1 2018-06-03 00:00:00+00:00 2019-09-28 00:00:00+00:00    324.195723
2 2020-01-28 00:00:00+00:00 2020-06-14 00:00:00+00:00     15.323172
3 2020-08-28 00:00:00+00:00 2022-02-20 00:00:00+00:00  11882.736154
4 2022-03-31 00:00:00+00:00 2023-06-06 00:00:00+00:00  -6896.369980

# Build a strategy to manage losing positions

In [36]:
# From documentation. this clarifies quite a bit
# Enter randomly, exit randomly but only if in profit
@njit
def signal_func_nb(c, entries, exits):

    # c.i is the current row. c.index[c.i] is the current timestamp
    ts = c.index[c.i] # c.index returns an array with timestamps in the nanosecond format while c.i returns the current row. By applying the latter on the former, we can get the current timestamp.
    is_entry = vbt.pf_nb.select_nb(c, entries)
    is_exit = vbt.pf_nb.select_nb(c, exits)
    if is_entry:
        return True, False, False, False
    if is_exit:
        print(c.last_pos_info[c.col]["return"])
        pos_info = c.last_pos_info[c.col]
        if pos_info["status"] == vbt.pf_enums.TradeStatus.Open:
            if pos_info["pnl"] >= 0:
                return False, True, False, False
    return False, False, False, False

data = vbt.YFData.fetch("BTC-USD")
entries, exits = data.run("RANDNX", n=10, unpack=True)
pf = vbt.Portfolio.from_signals(
    data,
    signal_func_nb=signal_func_nb,
    signal_args=(vbt.Rep("entries"), vbt.Rep("exits")),
    broadcast_named_args=dict(entries=entries, exits=exits),
    jitted=False  
)
pf.trades.records_readable[["Entry Index", "Exit Index", "PnL"]]

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
-0.3185888553301187
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
27

Entry Index                Exit Index          PnL
0 2014-11-01 00:00:00+00:00 2017-11-18 00:00:00+00:00  2291.457862
1 2017-12-23 00:00:00+00:00 2021-03-02 00:00:00+00:00  5479.467791
2 2021-06-07 00:00:00+00:00 2021-12-31 00:00:00+00:00  2989.232566
3 2022-03-11 00:00:00+00:00 2023-06-09 00:00:00+00:00 -3436.968488

In [5]:
# This will also come in handy 
# Joining the ranks of stop orders, time stop orders can close out a position after a period of time or also on a specific date.
# Enter randomly, exit before the end of the month

data = vbt.YFData.fetch("BTC-USD", start="2022-01", end="2022-04")
entries = vbt.pd_acc.signals.generate_random(data.symbol_wrapper, n=10)
pf = vbt.PF.from_signals(data, entries, dt_stop="M")  # Exit before the end of the month
pf.orders.records_readable[["Fill Index", "Side", "Stop Type"]]

Fill Index  Side Stop Type
0 2022-01-19 00:00:00+00:00   Buy      None
1 2022-01-31 00:00:00+00:00  Sell        DT
2 2022-02-04 00:00:00+00:00   Buy      None
3 2022-02-28 00:00:00+00:00  Sell        DT
4 2022-03-02 00:00:00+00:00   Buy      None
5 2022-03-31 00:00:00+00:00  Sell        DT

In [6]:
# Regular metrics such as MAE and MFE represent only the final point of each trade, but what if we would like to see their development during each trade? You can now analyze expanding trade metrics as DataFrames!
# Visualize the expanding MFE using projections
data = vbt.YFData.fetch("BTC-USD")
pf = vbt.PF.from_random_signals(data, n=50, tp_stop=0.5)
pf.trades.plot_expanding_mfe_returns().show()


In [7]:
# Limit and stop orders can also be defined using a target price rather than a delta.
data = vbt.YFData.fetch("BTC-USD")
pf = vbt.PF.from_random_signals(
    data, 
    n=100, 
    sl_stop=data.low.vbt.ago(10), # This is perfect for our double peak concept
    delta_format="target"
)
sl_orders = pf.orders.stop_type_sl
signal_index = pf.wrapper.index[sl_orders.signal_idx.values]
hit_index = pf.wrapper.index[sl_orders.idx.values]
hit_after = hit_index - signal_index
hit_after

TimedeltaIndex(['10 days',  '1 days',  '1 days',  '1 days',  '4 days',
                 '1 days',  '1 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '1 days',  '1 days',
                '15 days',  '1 days',  '1 days',  '3 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '2 days',  '1 days',
                 '1 days',  '1 days',  '1 days', '10 days', '26 days',
                 '1 days',  '9 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '2 days',  '1 days',
                 '3 days',  '3 days',  '1 days',  '1 days',  '1 days',
                 '1 days',  '1 days',  '1 days',  '1 days', '41 days',
                 '2 days'],
               dtype='timedelta64[ns]', name='Date', freq=None)

In [8]:
from numba import njit
import pandas as pd
import numpy as np
import talib
import vectorbtpro as vbt
from vectorbtpro.portfolio.nb.core import register_jitted, tp
from vectorbtpro.utils.template import Rep, RepEval, RepFunc

vbt.settings.set_theme("dark")
vbt.settings['plotting']['layout']['width'] = 800
vbt.settings['plotting']['layout']['height'] = 300

data = vbt.YFData.fetch(['SPY'], missing_index='drop')
TALIB_RSI = vbt.IndicatorFactory.from_talib("RSI")

  0%|          | 0/1 [00:00<?, ?it/s]

In [9]:


@njit
def produce_oscillator_signals(ind, entry, exit):
    signals = np.where( ind > exit, -1, 0)
    signals = np.where( (ind < entry), 1, signals)
    return signals

def custom_indicator(close, period = 14, entry_level = 30, exit_level = 70):
    rsi = TALIB_RSI.run(close, period).real.to_numpy()
    return produce_oscillator_signals(rsi, entry_level, exit_level)

ind = vbt.IndicatorFactory(
    class_name = "Oscillator",
    short_name = "osc",
    input_names = ["close"],
    param_names = ["period", "entry_level", "exit_level"],
    output_names = ["value"]
).with_apply_func(
    custom_indicator,
    period = 14,
    entry_level = 30,
    exit_level = 70,
)

my_signals = ind.run(
    data.get('Close'),
    period=2,
    entry_level=np.arange(10, 40, step=5, dtype=int),
    exit_level=np.arange(60, 90, step=5, dtype=int),
    param_product = True,
    execute_kwargs=dict(show_progress=True),
)
pf = vbt.Portfolio.from_signals(
    open=data.open,
    high=data.high,
    low=data.low,
    close=data.close,
    long_entries=my_signals.value == 1,
    long_exits=my_signals.value == -1,
    init_cash=10000,
    fees=0.0,
    fixed_fees=0.0,
    slippage=0.0,
    freq='1D',
    size_type='percent100',
    size=100,
    price="nextopen",
)

df = pf.stats([
    'total_trades',
    'profit_factor',
    'total_time_exposure',
    'win_rate',
    'avg_winning_trade',
    'avg_losing_trade',
    'avg_winning_trade_duration',
    'avg_losing_trade_duration'
], agg_func=None)


df["CAGR"] = round(100*pf.annualized_return,2)

df["CAGR/MDD"] = -1*pf.annualized_return/pf.max_drawdown

df = df[df["Total Trades"]>30]
df = df.sort_values(['Profit Factor'], ascending=[False])

display(df)

  0%|          | 0/36 [00:00<?, ?it/s]

Total Trades  Profit Factor   
osc_period osc_entry_level osc_exit_level symbol                                
2          20              85             SPY              416       2.102935  \
           25              85             SPY              463       2.079838   
           30              85             SPY              495       2.014538   
           10              85             SPY              283       1.956087   
           25              70             SPY              631       1.955809   
           20              80             SPY              473       1.950216   
                           70             SPY              548       1.931503   
           35              85             SPY              530       1.908858   
           10              70             SPY              336       1.896403   
           25              80             SPY              532       1.895021   
           15              85             SPY              363       1.886448   
           20              75             SPY              513       1.878896   
           30              70             SPY              692       1.864501   
           10              80             SPY              310       1.858277   
           25              65             SPY              670       1.844914   
           30              80             SPY              578       1.841502   
           25              75             SPY              583       1.840132   
           15              70             SPY              456       1.833171   
           10              75             SPY              322       1.822339   
           15              75             SPY              435       1.802949   
           20              65             SPY              581       1.796613   
           15              80             SPY              408       1.789161   
           30              65             SPY              749       1.786608   
           25              60             SPY              696       1.770993   
           15              65             SPY              480       1.761440   
           35              70             SPY              756       1.755246   
           20              60             SPY              601       1.752191   
           30              75             SPY              638       1.741729   
           10              60             SPY              350       1.741158   
                           65             SPY              344       1.733693   
           35              80             SPY              626       1.729398   
           30              60             SPY              785       1.727625   
           15              60             SPY              486       1.697658   
           35              65             SPY              823       1.685826   
                           75             SPY              693       1.624029   
                           60             SPY              862       1.612365   

                                                  Total Time Exposure [%]   
osc_period osc_entry_level osc_exit_level symbol                            
2          20              85             SPY                   48.410310  \
           25              85             SPY                   52.924244   
           30              85             SPY                   56.496140   
           10              85             SPY                   34.371320   
           25              70             SPY                   37.890881   
           20              80             SPY                   41.907628   
                           70             SPY                   33.625540   
           35              85             SPY                   59.256836   
           10              70             SPY                   20.829517   
           25              80             SPY                   46.434646   
           15              85             SPY  

In [10]:
best_profit_factor_params = (2,	10,	70,	'SPY')
print(pf[best_profit_factor_params].stats())
pf[best_profit_factor_params].plot().show()


Start                         1993-01-29 00:00:00-05:00
End                           2023-06-06 00:00:00-04:00
Period                               7643 days 00:00:00
Start Value                                     10000.0
Min Value                                   9907.403313
Max Value                                  80080.668979
End Value                                  80080.668979
Total Return [%]                              700.80669
Benchmark Return [%]                        1603.782546
Total Time Exposure [%]                       20.829517
Max Gross Exposure [%]                            100.0
Max Drawdown [%]                              30.596247
Max Drawdown Duration                 823 days 00:00:00
Total Orders                                        672
Total Fees Paid                                     0.0
Total Trades                                        336
Win Rate [%]                                  72.916667
Best Trade [%]                                11

In [11]:
best_tr_params = pf.total_return.idxmax()
best_tr_params

(2, 25, 70, 'SPY')

In [12]:
pf[best_tr_params].plot().show()